In [ ]:
import numpy as np

"""
데이터를 불러오고, 글자-벡터 간 상호 매핑 준비
"""

# input.txt (Coriolanus by William Shakespeare) 파일을 로드합니다.
data = open('input.txt', 'r').read()
# input.txt 파일 내에서 고유한 문자를 추출합니다 (unique)
chars = list(set(data))
data_size, vocab_size = len(data), len(chars)

print ('해당 데이터는', format(data_size, 'd'), '개의 글자로 이루어져 있으며,', format(vocab_size, 'd'), '개의 고유한 글자가 존재합니다.')

# 추출된 고유한 단어들을 알파벳 순서로 출력합니다.
print ('------------------')
print(repr(''.join(sorted(str(x) for x in chars))))
print ('------------------')

"""
고유한 글자들(a,b,c,d...,X,Y,Z)를 인덱스 숫자(1,2,3,4...)에 매핑하는 dictionary, 그 반대
"""
char_to_ix = { ch:i for i,ch in enumerate(chars) }
ix_to_char = { i:ch for i,ch in enumerate(chars) }

"""
hyperparameter를 설정합니다.
"""
hidden_size = 100 # 뉴런들의 hidden layer 크기
seq_length = 25 # RNN을 펼쳤을 때(unroll)의 단계 (a.k.a 학습 시킬 때 한번에 불러올 글자 수)
learning_rate = 1e-1 # 학습 속도, 가중치를 조정할 때 이동할 간격

"""
모델의 파라미터들을 초기화 합니다.
가중치는 작은 수의 랜덤한 값, bias는 0으로 초기화
"""
# rand : 0부터 1사이의 균일 분포
# randn : 가우시안 표준 정규 분포, 기댓값이 0이고 표준편차가 1인 가우시안 표준 정규 분포를 따르는 난수를 생성
# randint : 균일 분포의 정수 난수
Wxh = np.random.randn(hidden_size, vocab_size)*0.01 # input to hidden (100, 25)
Whh = np.random.randn(hidden_size, hidden_size)*0.01 # hidden to hidden (100, 100)
Why = np.random.randn(vocab_size, hidden_size)*0.01 # hidden to output (25, 100)
bh = np.zeros((hidden_size, 1)) # hidden bias (100,1)
by = np.zeros((vocab_size, 1)) # output bias (25,1)

def lossFun(inputs, targets, hprev):
  """
  inputs, targets - 숫자 인덱스의 리스트
  hprev - H(hidden_size)x1의 array, 이전 학습에서 반환한 마지막 hidden state
  
  forward pass(손실값 계산), backward pass(그래디언트 계산)을 모두 수행한 후에
  손실값, 각각의 가중치에 대한 그래디언트, 그리고 다음 반복 때 사용할 마지막 hidden state를 반환
  """
  xs, hs, ys, ps = {}, {}, {}, {}
  hs[-1] = np.copy(hprev)
  loss = 0
  """  
  forward pass, 손실값 계산
  """
  for t in range(len(inputs)):
    # 1-of-k(one-hot) 형태로 변환, 모든 값이 0인 array 준비합니다.    
    xs[t] = np.zeros((vocab_size,1))
    # 해당하는 글자에만 값을 1로 설정 - [0, ..., 0, 1, 0, ...,0]
    xs[t][inputs[t]] = 1
    # hidden state를 업데이트 합니다.
    hs[t] = np.tanh(np.dot(Wxh, xs[t]) + np.dot(Whh, hs[t-1]) + bh)
    # 다음 글자가 어떤 글자가 나올지 가능성을 표시한 array (정규화되지 않은)
    # np.dot - 내적곱 연산, np.matmul - 행렬곱 연산 / 2차원 행렬 곱셈에서는 서로 같은 기능을 수행하지만 고차원 배열이나 tensor를 곱할 때는 그 용법이 다르다.
    ys[t] = np.dot(Why, hs[t]) + by
    ps[t] = np.exp(ys[t]) / np.sum(np.exp(ys[t])) # probabilities for next chars
    loss += -np.log(ps[t][targets[t],0]) # softmax (cross-entropy loss)
  
  """
  backward pass, 그래디언트 계산
  """
    
  # 변수 초기화  
  dWxh, dWhh, dWhy = np.zeros_like(Wxh), np.zeros_like(Whh), np.zeros_like(Why)
  dbh, dby = np.zeros_like(bh), np.zeros_like(by)
  dhnext = np.zeros_like(hs[0])
  
  # forward pass의 과정을 반대로 진행 (t=24부터 시작)
  for t in reversed(range(len(inputs))):
    dy = np.copy(ps[t])
    # y의 그래디언트 계산, softmax 함수의 그래디언트 계산
    dy[targets[t]] -= 1
    dWhy += np.dot(dy, hs[t].T)
    dby += dy
    # loss에서 사용된 h와 h를 업데이트한 계산의 그래디언트 값을 더함
    dh = np.dot(Why.T, dy) + dhnext
    # tanh 역전파
    dhraw = (1 - hs[t] * hs[t]) * dh
    dbh += dhraw
    dWxh += np.dot(dhraw, xs[t].T)
    dWhh += np.dot(dhraw, hs[t-1].T)
    dhnext = np.dot(Whh.T, dhraw)
  for dparam in [dWxh, dWhh, dWhy, dbh, dby]:
    # 그래디언트 발산 방지
    np.clip(dparam, -5, 5, out=dparam)
  return loss, dWxh, dWhh, dWhy, dbh, dby, hs[len(inputs)-1]

def sample(h, seed_ix, n):
  """ 
  모델에서 지정된 글자 수(n) 만큼의 글자(숫자의 리스트)를 출력
  h - hidden state
  seed_ix - 주어진 첫번째 글자
  """
  x = np.zeros((vocab_size, 1))
  x[seed_ix] = 1
  ixes = []
  for t in range(n):
    # forward pass 수행
    h = np.tanh(np.dot(Wxh, x) + np.dot(Whh, h) + bh)
    y = np.dot(Why, h) + by
    p = np.exp(y) / np.sum(np.exp(y))
    
    # 샘플링. 임의성을 부여하기 위해 argmax대신 array p에서 주어진 확률에 의해 하나의 문자를 선택
    ix = np.random.choice(range(vocab_size), p=p.ravel())
    
    # 다음 글자 추론을 위해 샘플링 된 글자를 다음 입력으로 사용 
    x = np.zeros((vocab_size, 1))
    x[ix] = 1
    
    # 결과값 리스트에 추가
    ixes.append(ix)
  return ixes


#  반복 회수(n) 및 입력 데이터(p) 위치 초기화 
n, p = 0, 0

mWxh, mWhh, mWhy = np.zeros_like(Wxh), np.zeros_like(Whh), np.zeros_like(Why)
# Adagrad 방식을 채택하기 위한 메모리 변수
mbh, mby = np.zeros_like(bh), np.zeros_like(by)
# 학습이 이루어지기 전의 손실값, iteration == 0 일 때
smooth_loss = -np.log(1.0/vocab_size)*seq_length
while True:
  # 입력데이터 준비, 텍스트의 맨 앞쪽(왼쪽에서 오른쪽)부터 seq_length만큼씩 데이터를 준비
  # 데이터를 모두 사용하면 입력 데이터의 맨 처음으로 이동
  if p+seq_length+1 >= len(data) or n == 0: 
    # RNN 메모리 초기화
    hprev = np.zeros((hidden_size,1))
    # 입력 데이터의 맨 처음으로 이동
    p = 0
    
  # 입력(p~p+24번째 글자), 목표(p+1~p+25번째 글자) 데이터를 준비
  inputs = [char_to_ix[ch] for ch in data[p:p+seq_length]]
  targets = [char_to_ix[ch] for ch in data[p+1:p+seq_length+1]]

  # 학습을 100번 반복할 때마다 학습 결과를 출력
  if n % 100 == 0:
    # #지금까지 학습한 RNN을 이용하여 숫자의 리스트를 출력
    sample_ix = sample(hprev, inputs[0], 200)
    txt = ''.join(ix_to_char[ix] for ix in sample_ix)
    print ('----\n', format(txt, 's'), '\n----')

  # 손실함수에서 손실값과 그래디언트를 함께 계산
  loss, dWxh, dWhh, dWhy, dbh, dby, hprev = lossFun(inputs, targets, hprev)
  smooth_loss = smooth_loss * 0.999 + loss * 0.001
  if n % 100 == 0: print ('iter', format(n, 'd'), ', loss : ', format(smooth_loss, 'f')) # 진행사항 - 반복횟수, 손실 출력
  
  # Adagrad 방식으로 파라미터 업데이트
  for param, dparam, mem in zip([Wxh, Whh, Why, bh, by], # 가중치
                                [dWxh, dWhh, dWhy, dbh, dby], # 그래디언트
                                [mWxh, mWhh, mWhy, mbh, mby]): # 메모리 
    mem += dparam * dparam
    param += -learning_rate * dparam / np.sqrt(mem + 1e-8) # adgrad 방식으로 실제 파라메터 업데이트

  p += seq_length # 데이터 포인터를 seq_length만큼 우측으로 이동
  n += 1 # 반복횟수 카운트


data has 1115394 characters 65 unique
----
 UahRN,:fRU,RkSHTUmzSqtrWeo;w&LIvm:F?NjUbPxjjT'
GWahy3pMclaEI
NVq!MT:'czOE wA:DVaRMgJtBt3ovV,T,oLi;umdDcjqa FReb
$LI-I3?fsadSFnD:JKAHIfjx$THh&SPm.P bgBkVilqS3CVFxltI$shOcUg'Diyt&JU?qTDcPtgPqGFjKAMx$CEO 
----
iter 0 , loss :  104.359681
----
 hu :oeel u aplort ehln
eh 
rahsl si

y,eoawlA WAhabrkmhupe
nsssdrmth nahhhWCnsh Aalth vdorEltok uwcktkoCoa  bCs knssClne s   neco:
eee bohnpp:nnsh v
rv r owi p kh
dsrdstfecka s sY
tiBe
rsy sossu ohhtl 
----
iter 100 , loss :  104.021756
----
 reeniEhesmTco eulstiyvtrtu Foby ecg I fkv wyk 
Ou ttoge asogs
i cgi e  prse t wremotaetmty tz
ahiad oi
bltoi-eh'lTiisndneatsoyho u hl.
ct  e tn.heU,hoeei
fotnecThee nLhhhpfWNgetao ne?,tirteyciset uh a 
----
iter 200 , loss :  102.346472
----
 tyaauaoyyOi 'ontm?WAu!stroea
ySA CwieohvU fAunotthe r
tto

f lis
UWyophUbA
l rIsabeigoneawisnC ,w
a hfu;s
fuculHriXN Naifh
CeUl?A
e
rteCrtm 
hStSzbNnf?kuwurdMtt w
 ehu y 
auUpkn.
 a sCrhUesle?wAacrig' 
----
iter 300 , loss :  100

----
 sse ritres Ronr net' idd reven: I in, bhiulr, bht.
Buk warno donE
Brtt tis wige ta pith the lave thas basiln.
I on, thyed,
cil,. hem, dofre hare
Yomy onf.

whoonme t he msence the ttavep thand
That fo 
----
iter 3400 , loss :  63.168049
----
 
GONENINIUS:
Iflumsigong
Ans yu
corth.
And, dise iul.
Mhe nouen'nd
Th an or mowc. eus warg kout
Tot foe th,d arer tor, dis, hove the
Domt

Sact simind moverriz wouve thurhe;
Hond!
jiur to is mef helus 
----
iter 3500 , loss :  62.632638
----
 us ce, mit, ci rhof wume ail ghepe mith
Avir ord fruruti le miveres wyos a northis t theld thamd inle ther n mint at.

OCOxOENENIUS:
Cons toen tuy lo hichan
Terrmem, seun wad metciilghelalcont iller l 
----
iter 3600 , loss :  62.342554
----
 OLUS?
NEwIUS:
Wee, ancine soud ere ho bupa salt aves ging, lers vonis and.
Lucone in hrer hot te ands puule
Bope casn ciths,
Meafs, uly hithize

CORDSathe: thous, seck coode belitt.
Tova tats ko th yo 
----
iter 3700 , loss :  61.901978
----
  pelats,
Hid ane
Fi be

----
  werented mergend thou ss, ghoupun,
Thm forten the !o wroron. st Ess sad in ffyt
Anend?

GLCECokeas chape kiinb.
Werl Hey sorh thaberb. I by moopy thow agwere ti paars, worltve mwar wee iwies
Grithew  
----
iter 6800 , loss :  58.088641
----
 yok Rlenes heard cmyowend oulthorn:.

GTOurl'd hithor teat fethe? Mom mid and babuh tors for mul nanche frelugrinongbl neth.

LGEO:
At thayen nochiu.
What yny kod tad wivaviven un?
Thay ise-I
Agrcllis 
----
iter 6900 , loss :  57.633471
----
 vithoutys:
snourssot kild fow ind se hpreedcrno fory sis thord loee y'on,
Ande: uraverm!
Gwham.

MSjIUTUS: Antes win sle, l in,
Ally ks mone ole, mut.

VCECEDKoR?

LLERARAVY:
Lour nt, dradci, hy were  
----
iter 7000 , loss :  57.896327
----
 EETrarg ne torr I drak' hereofbun, walck elll.

GER:
Seor Ibddse thor wi! or gxir wed bare hy id unte sire doge he thipast ard tencs licm heve yare ingemaykvetseanger damur cernomes afowems, anen bed  
----
iter 7100 , loss :  57.920428
----
 l cruvangh
To soa cors

----
 Your, hagl theicd eithenFese, ice wod of the sabls.

BUCKINGMAD:
Tu!
Neanlligh cour wouls cawrul your ward set of or,
wo locerk arllx aln guta the the fereror of e in mom sho slree wimh yanguthe
Oryor 
----
iter 10200 , loss :  54.447855
----
 n ERxale', thim'd:
Ane the.

BUCERYINGHAM:
Thar und Andt If? waghdinke
I to ftarb noy'y that,
To the.il gike,
Hy I rord the whac,
As tho tove, coye rening,
And to hy yout stonghiu ind Outos I phat ans 
----
iter 10300 , loss :  54.420800
----
 chdem:
Whecice;
Guvesiseres har llorderd will my wors doll qu end ald sethe yow thau:
Wo Eth o'd youred-po bablly tron thin an,
grecling cortu tis mive wer in forin I porstett that
Thert, pod hy lus,  
----
iter 10400 , loss :  54.256900
----
 ITECICASTE:

CESYOLANN:
Mind heen,
I,
but remis ching th in wien, fad titl'd hew;
Foclane, wlat of gence sote yout ur what of the muecher tham heer-Hik.

GROBRUS:
Bithert have thand copame,
Thll theal 
----
iter 10500 , loss :  54.230336
----
  tt;
Anntue'.
Cede

----
  in trake cur, grint indt the kincin so nor shind Rod Ro ald bhouse be Bundy buiser nlether shis fuvend'g tume bren, wiin oint youne
Tiet, bieour:
Nowe ousby my for liune ma hekp bmy erew sa's noving  
----
iter 13600 , loss :  54.274205
----
  oup on kin with noa harn ome thou sien gols hise ther goh wpood ame my Wheak preins csespus, devel hit sur hyace,
Th. Tord, me, nin qoderave pescirt frestad:
And fopteng ou'd,
Hits goog thet,
Buthent 
----
iter 13700 , loss :  54.256364
----
 des'ssure theclou fon,
Whoule
What cound'gh Jencesned wragruinche
Ty of pelchildalu yom fis't-st.
Wloufraglses; my brordide, thin nourceail,
Ane wawrlere hou to paupdin then illy Iod'd buce'ch wertes  
----
iter 13800 , loss :  54.221371
----
 ow soed goweliyn
Soma, fhiggen theyen Narikes.

KEN!
BKN IING ROABROF Be I YOLI:
Or Tourise tro widis.

Hey Ghe rracn walld erdbra, my ilf's meveug to tart shyolst sorlswonn' bul lought- pin hakf, im  
----
iter 13900 , loss :  54.126876
----
  goap?

KI GBMENGA

...

----
 Masible ward as be, hang us Come hiss thy brother look: you prown.

ELBRLIO:
Mercyding Becods
I day haveisickears;
Now to my son he bilty spere daon do your againd hust grombook thas and of trenged:
A 
----
iter 1645600 , loss :  43.415983
----
 u hees of such Pale, or hand that conter his frat's saw.
Thy
like.
O,
May us as the guent yets comingistor:
Goodly abdread is as unoth
he best
aland.

DUCELBAUTINGHANDET:
My gord: burgils:
I pit; I ha 
----
iter 1645700 , loss :  43.416374
----
 oth.

KING RICERSARELLA:
A hander:
Ifle.

Thm't in Heness in hand and shall hargefious prons, more;
Let his polleed and be part: selice
So merdinue: so get are thine,
I emises far owe may and take on
 
----
iter 1645800 , loss :  43.676695
----
 if dighdur; A peemeningy you sir,--

NURENCE RIONGE NI:
Gind, our were seation tike and poservicknte?

FR:
Come;
And,
Make from wose, polloy:
A daudies
Unot as fless
and bear Nop thresp the juster.
Pr 
----
iter 1645900 , loss :  43.915059
----
 
I'll not 

----
 ee-nicg prothard,
To ploceats
Ander, a'll scaurdent. I many the 'twaid sleale requessent and day
An of my is the seepl all your law a pracy,
Where so do me?
Mare lenes?
Hastul thas infort a be
To my l 
----
iter 1649000 , loss :  41.921467
----
 ffrest
A more ontel.

Pustellod's, that thee, I love will ap comive:
Thou drucon,
shy to stam.
Did madess: wishen.
To fele by thy tour-ont choent! I could?

MONTION ELY IS:
Why: not dught to sigius,
S 
----
iter 1649100 , loss :  41.719178
----
 bate you leas fret not and so his bate the savilly, ant knirsonger.

MTISSIO:
That be the fear with sie;
To the desewen;
By thoun Offrother? King survant him seevatiosfo;
For see that truck'd Jose, fo 
----
iter 1649200 , loss :  41.323484
----
 sior in their prospial in are Ihat; sunruss lo;
for smeret to theil maunce.

ISABELLA:
If Dorvient trush sicus be dends oppedy well:
Sicnochter a go none.

PETRUCHIO:
Has aur aster? o'ty sir:
I would  
----
iter 1649300 , loss :  41.424318
----
 s they wen

----
 instrus by you lead, and here,
No infime fo me
sousing, wits a tuise, hath
Boond not the witht
hull let.

MARCAUNES:
What shall a chopeisome
To my kink' brows??

Sedizends to would give you! I am, our 
----
iter 1652400 , loss :  44.097754
----
 and vecy, what itlong.
Would bood:
The vary haberth.
Cet ravone
But the a dads, ammith oft hall well'd I bach yours prate.

MENENARNIUS:
What fraer
Vircest,
I hon he'le faller speak,
Shall do sit Lond 
----
iter 1652500 , loss :  44.008137
----
 jud.

COMIET VI:
Your crove bockne compand
Upoutch,
And more chalied
Hark, loor of prant quive griend no, Agyst!

CLUFRINGHAN:
Has that appickstermed, wher, than not ridcers

LUCIONA:
True;
Whoch bet' 
----
iter 1652600 , loss :  43.989417
----
 m it shall to-sucting bed:
You thought,
Tome
lest treave, wherencher eartone, Whas.
Or spory young usaled Catishaca.

Skius and cast you that hence;
My moants; grocliglust, I'll coubcally you, good lo 
----
iter 1652700 , loss :  43.905820
----
  me; hour.

----
 , sound prevaits!

LUCIONTNA:
Hack'd of his a myself thy sowe our frovesbrounce
are you so tale faughts is their puss be never, thou nome greaty and light my some, the pray Maininy fringilly, panatink 
----
iter 1655800 , loss :  42.515878
----
 our but of such day'st them to his course; and crach
ase,
She for us what it in him, her I hate care:
This be be shall woundentys Behost uspes
Mare of the flom I doon this?

CORIOLUCESTY:
Now
To is se 
----
iter 1655900 , loss :  42.430987
----
 ndrown traused:
What go yours fatheralad,
But did revemion, Cetort of my swiousess
My guesess compaining the words to it him, you good go not prien Jod! and mowe adion:
A cuss, that marce.

CORIOLANUS 
----
iter 1656000 , loss :  42.264897
----
 pountence come care, I feven,
Mersion mo hen on some hangs faesseft tho'then I she my kinks:
Ty shall cennerd, sury for show upon own wase: in the futle:
Backs. Your hense, wates, Your tailoning
Of th 
----
iter 1656100 , loss :  42.441017
----
 nom fauned

----
 words,
Yet then to purrt
my him.

BRPAENCE:
I how lut maketice sair be gulliem you them: ginge, my handulastined exchinguon Lady
cay, never, the more in the ewer losart whech-coge are common when hero 
----
iter 1659200 , loss :  41.993919
----
 
Wightors theee a duaidhars, dear cander's in macky, and friy,
By Romeablin'd deseent for theue your regair my righe,
When bucks: aftices now:
He state, for not, is afole both frial:
A
dank; I coul no 
----
iter 1659300 , loss :  41.988836
----
 ipery fearts,
Withine ware.
As find suth, 'twer unnetion, we promnce of thinks indeked the in.
If worst and seace.

BIANGER:
Sole prinquesty.
And I, not to brived is for the juds
This to him, my curd  
----
iter 1659400 , loss :  41.986799
----
 he vidmafferled no stuighss dreavety: surjoed's house
Freive; but whese good after misirevong my wordzeor go now,
Sirsefs alther nour so: so wito;
When be tam ap duasong?
Beely:
How uncan'd, but gentl 
----
iter 1659500 , loss :  41.901532
----
  shall the